In [2]:
import re
import json
import math
import datetime
import requests
import urllib.request
import urllib.error
import urllib.parse
from bs4 import BeautifulSoup

In [3]:
naver_client_id = "lzPSlFTEnz232oLdqwzy"
naver_client_secret = "1Ig7U84bjP"

In [5]:
def naver_blog_crawling(search_blog_keyword, display_count, sort_type):
    search_result_blog_page_count = get_blog_search_result_pagination_count(search_blog_keyword, display_count)
    get_blog_post(search_blog_keyword, display_count, search_result_blog_page_count, sort_type)


def get_blog_search_result_pagination_count(search_blog_keyword, display_count):
    encode_search_keyword = urllib.parse.quote(search_blog_keyword)
    url = "https://openapi.naver.com/v1/search/blog?query=" + encode_search_keyword
    request = urllib.request.Request(url)

    request.add_header("X-Naver-Client-Id", naver_client_id)
    request.add_header("X-Naver-Client-Secret", naver_client_secret)

    response = urllib.request.urlopen(request)
    response_code = response.getcode()

    if response_code is 200:
        response_body = response.read()
        response_body_dict = json.loads(response_body.decode('utf-8')) # 긁어온 내용 

        if response_body_dict['total'] == 0:
            blog_pagination_count = 0
        else:
            blog_pagination_total_count = math.ceil(response_body_dict['total'] / int(display_count))

            if blog_pagination_total_count >= 1000:
                blog_pagination_count = 1000
            else:
                blog_pagination_count = blog_pagination_total_count

            print("키워드 " + search_blog_keyword + "에 해당하는 포스팅 수 : " + str(response_body_dict['total']))
            print("키워드 " + search_blog_keyword + "에 해당하는 블로그 실제 페이징 수 : " + str(blog_pagination_total_count))
            print("키워드 " + search_blog_keyword + "에 해당하는 블로그 처리할 수 있는 페이징 수 : " + str(blog_pagination_count))

        return blog_pagination_count


def get_blog_post(search_blog_keyword, display_count, search_result_blog_page_count, sort_type):
    encode_search_blog_keyword = urllib.parse.quote(search_blog_keyword)

    for i in range(1, search_result_blog_page_count + 1):
        url = "https://openapi.naver.com/v1/search/blog?query=" + encode_search_blog_keyword + "&display=" + str(
            display_count) + "&start=" + str(i) + "&sort=" + sort_type

        request = urllib.request.Request(url)
#         print('okay')
        
        request.add_header("X-Naver-Client-Id", naver_client_id)
        request.add_header("X-Naver-Client-Secret", naver_client_secret)

        response = urllib.request.urlopen(request)
        response_code = response.getcode()

        if response_code is 200:
#             print('okay')
            response_body = response.read()
            response_body_dict = json.loads(response_body.decode('utf-8'))

            for j in range(0, len(response_body_dict['items'])):
                try:
                    blog_post_url = response_body_dict['items'][j]['link'].replace("amp;", "")
#                     print('okay')
                    
                    get_blog_post_content_code = requests.get(blog_post_url)
                    get_blog_post_content_text = get_blog_post_content_code.text

                    get_blog_post_content_soup = BeautifulSoup(get_blog_post_content_text, 'lxml')

                    for link in get_blog_post_content_soup.select('iframe#mainFrame'):
                        real_blog_post_url = "http://blog.naver.com" + link.get('src')
                        
#                         print('okay')

                        get_real_blog_post_content_code = requests.get(real_blog_post_url)
                        get_real_blog_post_content_text = get_real_blog_post_content_code.text

                        get_real_blog_post_content_soup = BeautifulSoup(get_real_blog_post_content_text, 'lxml')

                        for blog_post_content in get_real_blog_post_content_soup.select('div#postViewArea'):
                            blog_post_content_text = blog_post_content.get_text()
                            
#                             print('okay')
                            print(blog_post_content_text)
                            if blog_post_content_text is None:
                                print('No text !')
                            remove_html_tag = re.compile('<.*?>')

                            blog_post_title = re.sub(remove_html_tag, '', response_body_dict['items'][j]['title'])
                            blog_post_description = re.sub(remove_html_tag, '',
                                                           response_body_dict['items'][j]['description'])
                            blog_post_postdate = datetime.datetime.strptime(response_body_dict['items'][j]['postdate'],
                                                                            "%Y%m%d").strftime("%y.%m.%d")
                            blog_post_blogger_name = response_body_dict['items'][j]['bloggername']
                            blog_post_full_contents = str(blog_post_content_text)
                            
                            print('here')
                            
                            print("포스팅 URL : " + blog_post_url)
                            print("포스팅 제목 : " + blog_post_title)
                            print("포스팅 설명 : " + blog_post_description)
                            print("포스팅 날짜 : " + blog_post_postdate)
                            print("블로거 이름 : " + blog_post_blogger_name)
                            print("포스팅 내용 : " + blog_post_full_contents)
                except:
                    j += 1
                    print("Oops!")


# if __name__ == '__main__':
naver_blog_crawling("성심당 여행 주말에", 100, "sim")

키워드 성심당 여행 주말에에 해당하는 포스팅 수 : 1344
키워드 성심당 여행 주말에에 해당하는 블로그 실제 페이징 수 : 14
키워드 성심당 여행 주말에에 해당하는 블로그 처리할 수 있는 페이징 수 : 14


21년 4월 17일 : 대전여행다른 친구들 이야기 들어보면 사촌들과의 관계는 친구들보다 좀 벽이 있고 특별히 어려운 관계는 아니지만 그렇다고 일부러 연락해서 만나고 그러기엔 엄청 어색하다고..우리 집안이 좀 이상한건지 대부분의 사촌동생들과 아주 친하게 지낸다.자주 연락하고 같이 식사, 술 마시고 거리낌 없이 집에서 자고가기도 하고..아... 참고로 아버지 집안의 형제가 7남매 + 어머니 집안은 8남매 대부분 2명의 자녀라 내 사촌들의 수는 엄청나다.. 크큽..사회 초년생의 사촌들은 아무래도 내가 삼촌같아서 잘 어울리긴 힘들고나이가 엇 비슷한 사촌들과 좀 더 친하긴 하다.그 사촌 동생들 중 JH이라는 사촌이 있는데 오랜기간 공부하고 연구해서 박사가 되더니최근까지 서울에 대학에서 연구를 하다가 올해 대전에 있는 연구소로 취업을 하였다.회사에 있는동안 오피스텔이나 기숙사에서 지낼걸 생각했더니 이래저래 해서 대전 둔산동에 집을 매입했고 내부 인테리어 마쳤다고 했다.집들이도 할겸, 동생 취업도 축하도 할겸마침 날씨는 좋은데 주말에 몸이 근질근질 하기도 했고1년정도의 장기간 코로나로 집에 더 뒹굴면 진짜 우울증 심하게 올것 같은 느낌이였다.그렇게 토요일 오후 차를 끌고 대전 둔산동 사촌집으로 갔다.야탑에 있는 회사에서 출발하였는데 2시간 좀 넘게 걸렸다.고속도로는 막히지 않았는데 혼자가려니 엄청 지루했다.둔산동 동생집 주차장에 차를 세우고 간단히 집 구경을 하고 대부분 만족스러웠지만정리 빈약한 부분 오지랍 하면서 갈구기도 하고 식사를 하러 나왔다.출발 전부터 오늘은 이상하게 양꼬치가 먹고 싶었다.지글지글한 양꼬치에 맥주가 너무나 땡기던날..사실 난 대전과 연관되는게 없어 주기적인 방문은 없다.- 주말에 필 받아서 친구랑 성심당에서 빵먹고 오기.- 바람쐬고 싶으



[당일 대전여행/당일치기 여행/대전 빵집 성심당]왜 유명한지 알것 같은!주말에 쿠니가 앞으로 한동안 멀리는 못나갈테니 가깝게 대전을 다녀오면서 바람이나 쐬자며 급 결정!!뭔가 여행은 언제나 기분 좋은 거 같아요 ㅋㅋㅋㅋㅋㅋ중간에 휴게소두 들려서 간식거리도 좀 먹어주구~가서 맛있는 점심식사를 하구 요기조기 구경하구~성심당가서 빵세례도 좀 해오구 말이죠!!!근데 이날 쿠니 꿈에서 비행기가 추락하구제 꿈에서는 운전하다 자동차사고가 났었는데이날 하루종일 뭔가 엎지르는 일이 생기는거에요!!!!!!!!!!!!!!휴게소 내리면서 쿠니가 옷이랑 차에 아메리카노 엎질러버리구 ㅠ음식점에서 파스타먹다 제가 쿠니옷에 파스타궁물 엄청 튀겨가지구 닦느라 고생하다쿠니가 콜라를 제 옷에 또 엎질러버리고.............마지막에 돌아가면서 쿠니차에 있던 향기나는 양갱이 숯들이 들어있던 통이 있었는데그게 완전 엎질러지면서 중간에 청소기 끄내서 청소하고 ㅠㅠ정말 무서운 하루였답니다................흐흐.................................여튼 잠깐 딴길로 샜는데!!!!바로 후기 나갈께용 ㅋㅋㅋㅋㅋㅋ ​​​먼저! 여행의 묘미는 휴게소겠죠?!!잠깐 들려서 제가 조아하는 츄러스좀 사먹어주구~~~~요기 츄러스 제스타일이라 넘 좋아요 ㅠㅠㅋㅋㅋㅋ​​그리구 도착해서 점심먹구 성심당으로 향했어요!저희는 본점으로 갔습니다 ㅋㅋㅋㅋ

성심당 본점대전 중구 대종로480번길 151588-8069성심당에서 만원이상 사시면 한시간 무료주차권을 받으실수 있어요!!근처에 이안과병원 주차장에다 대시면 됩니다 ㅎㅎㅎㅎ​​​​​​​와.. 보기만해도 사람들 바글바글하네요 ㅠㅠㅠ정말 지나가기조차 힘들었던....​​​​​ ​​​​​​​성심당을 처음 오시는 분들을 위해요렇게 베스트메뉴로 정리도 되어있네용! ㅋㅋㅋㅋㅋ​저 우유고로케 먹어보구 시푼.. ㅠㅠ​​​​​​​​​​​​​​샌드위치랑 부추빵 순크림빵! ​​​​​이것저것 맛있어보이는 빵들 투성이네요 ㅠㅠ​ 요기는 고로케종류들과 주먹밥, 바게



+대전 동물원/성심당/가온레지던스 호텔+이웃님들~ 벌써 한주의 반이 지났어요ㅎㅎ조금만 힘내서 주말을 맞이 하면좋을 것 같아용 ㅎㅎ지난주 주말에 저는 대전에 다녀왔어용대구에서 조금 멀지만 한번도안가본 도시라 예전부터너무 가고싶었답니당 ㅎ동물원도 유명하다고 해서 완전기대하고 갔어요+_+첫날은기대했던 오월드오월드는 사실 놀이기구는 많지 않았어요어른들이 탈만한 놀이기구는 자이로드롭이랑 후룸라이드 정도 ㅎㅎ저는 두개 다 탔는데 오랫만에 타서 그런지 완전 신나더라구요*-*그리고 기대했던 사파리 ㅎㅎ버스 타고 이렇게 사파리 가는 거 처음 이었어요 그래서 엄청 기대하면서 갔답니다.버스를 타면 기사님께서 어떤 동물을보러 가는지 자세히 설명 해 주신답니당 처음엔 곰을 보러갔어요 과자 주는거 받아먹고 몇마리는 잠만 자고 있었죠 ㅋㅋㅋ가까이서 이런 야생의 동물들을본다는게 정말 재미있고 신기하더라구요 오월드 사파리에는 곰,사자,호랑이,기린등다양한 동물들이 있어요 생각보다 빨리 끝나긴 하지만재미있었어용 ㅎㅎ사파리 안에만 있는줄 알았던 동물들은 다른 곳에도 있더라구요 낙타,늑대,사막여우등 많은 동물들을 만날 수 있어요 ㅋㅋ다 보고 숙소로 돌아왔어요 대전에는 오피스텔형의 호텔이 많다고하더라구요.여긴 가온레지던스 호텔인데 펜션처럼 조리 시설이 되어 있어서 음식을 해서 먹을 수 있어요.객실 내부도 깔끔하고 넓은 편이어서 하루 정도 묵기에딱 좋았어요*-*쇼파는 펴지는 거라누워서 티비 보기도 하고 주방도 넓어서 음식 하기에도 편리했답니다.대전에 여행 가시는 분들은 참고 하셔도 좋을 것 같아요+_+다음날은 대전가면 꼭 가야한다는성심당 다녀왔어요*-* 튀김 소보로 꼭 따뜻할 때 먹고 싶었는데 소원이루었죠 ㅋㅋㅋ튀김 소보로는 기본으로 한통 사고 부추빵이랑 맛있어 보이는 빵들몇개 더 샀어요^-^ 너무 맛있어서 차 타자마자뚝딱 해치웠어요 ㅋㅋㅋㅋ빵들이 어쩜 다 그렇게 맛있는지 성심당 때문에 대전에 살고싶어 지더라구요ㅠㅋ성심당 갔다가시간이 조금 남아서 어제 못본 오월드튤립 축제도 가 봤어요 꽃을 보니 



LP판 사러간만에 대전역 근처에 나간김에은행동에 성심당에 들렀어요어차피 갈데도 없어서요... ㅋㅋㅋㅋ대전맛집! 하면 일.단.은 성심당이졍:)

은행동 성심당 본점 입니당 :)아...  꼭대기 짤림 ㅋㅋ어릴때부터 이 자리였는데건물이 많이 멋져졌어요 ㅎㅎ넘 오랜만에 갔나봐요동네 빵집이었는데 넘 치명적으로 변함 요런 분위기밖에서 보니 사람들 북적북적포토존으로 거대 튀김소보로 모형만들어놨더라구요ㅋㅋㅋㅋㅋ아......네.....음......뭥미 했지만솔직히 한컷 찍고 싶었음 ㅋㅋㅋ문앞에도 돌띵이로 성심당!들어가는 입구 발밑에도 성심당!!ㅋㅋㅋ무려 평일 애매한 시간도 이렇습니다발 디딜 틈이 없어요 ㅋㅋㅋㅋㅋ 헐 ㅋㅋㅋ뭔 빵들을 일케 드시나 ㅋㅋㅋ하긴 빵 안좋아하는 저도 은행동에 나오면 성심당은 꼭 들르니까말 다했죠 뭐다양한 종류의 빵들제가 은근 전국 맛난 빵집은 많이 가봤는데정말 솔직히..... 대전 사람이라 하는 말이 아니라정말 성심당이 맛있어요 진짜예요 ㅋㅋㅋ제가 알기로 성심당은대전역과 롯데백화점에 분점이 있어요맛은... 다른지 같은지 모르겠고요~요건 성심당에서 젤 유명한 빵 중 하나인부추빵!!!아우 맛나 보인다 ㅋㅋㅋㅋ근데 멀리서 오신 분들이 요거 사가시는건 비추!!따뜻할때 먹어야 맛나욥!중앙에 보이는 (보이세요? ㅋㅋㅋ 통통한분 배 쪽으로 보이는 빵)쏘세지 박힌 빵 대박 맛나요 냥이씨 추천!!!요건 다른 빵과 다른 위치에 있으니잘 찾으셔야함요부추빵과 튀김소보로(일명 튀소)는세트상품이 있더라구요전국에 택배로 배송도 가능한듯(?)긍데 둘다 멀리서 배송받아 드시면별로 맛없.....(을 거라는 예상)냥이씨와 저는 주말에 먹을 빵 몇개 사고배가 고파 2층으로 올라갔어요2층은 테라스 키친이라는 식당임다넓은편이구요좌석도 분위기가 다양해요올만에 가보니공기정화 식물이 곳곳에 되게 많이놓여있어서 므흣했네요 ㅎㅎ스파트필름 천지 캬~메뉴임다  늘 느끼지만 ㅋㅋ성심당 네임밸류에 비해 꽤 저렴해요대부분 6000원대부터~오픈 키친이라 조리하는 모습이 보여요사람이 많을땐 줄 서 기다리는데



대전성심당/튀기소보루/판타롱부추빵 완전 맛나!
 
 
 
주말에 대전을 다녀왔지요~
친구동생의 결혼식이 있어 부랴부랴 토요일 퇴근후 대전행 KTX에 몸을 실었어요.ㅎ
오랜만에 기차탄거라 좀 많이 신났어요..ㅎㅎ
여행을 가거나 그런게 아니라 지극히 개인적인 행사여서 사진도 없고..ㅠㅠ
그래도 다행히 대전에 그유명한 대전 성심당에 입문~*
대전성심당 본관엔 너무 줄이 길어서 
대전역에서 기차타면서 사야겠다고 결정!!
 

 
"맙소사.....설마...!!!!!"
진짜다...줄서있다...

 
 
대전역에도 서있다..휴우....ㅠㅠ
그냥 사야지....
줄서야지....
저는...반반박스!!구입했어요~~
 

 
득템하고 룰라 랄라~~~~~
홍홍홍~~~
호잇호잇!!!ㅎㅎ(빵은..언제나...옳죠!)
 
 

 
박스도 맛깔난다잉!!ㅎㅎ
아!!너무 유명하니까...
대전 성심당은 능력자....!!!!
 

 
 
요 때깔 좋은 튀김 소보루!!!아주아주아주 바삭해!!너는!!!ㅎㅎ
튀김소보루 너무 유명하죠?
특허까지라....!!!
일반 소보루를 튀김옷이 있어서 바삭바삭한!
그리고 안에 꽉 찬 팥까지!!!+_+
 

 
그리고 상상한것 이상으로 부추 폭탄!!!
판타롱 부추빵빵!!
대전성심당에서 튀김소보루와 어깨를 나란...나란히는 아닌것같아 사실-
넌 2위야.ㅎ
그래도 상당히 맛나요 이거-오묘하게 중독성있고 건강건강해지는 맛!!
 

 
실제로 정말 부추가...!!!!
비쥬얼 쇼크!!ㅎㅎㅎ
 

 
다른 빵들도 상당히 맛있어요~
 

 
대전에서 출발하는 기차를 타는 분들..!!
98%는 모두 성심당 종이백을.!!!
 
 
 
 
 
 


here
포스팅 URL : https://blog.naver.com/monade3513?Redirect=Log&logNo=40208994080
포스팅 제목 : 대전성심당/튀김소보루/판타롱부추빵 완전 맛나!
포스팅 설명 : 성심당/튀기소보루/판타롱부추빵 완전 맛나! 주말에 대전을 다녀왔지요~ 친구동생의 결혼식이 있어 부랴부랴 토요일 퇴근후 

...



안녕하세요퐁퐁이에요 



다들 빵 좋아하나요!? 정말 빵은....전국의 맛집 빵을 먹어봐야하나..어딜가도 맛있고. 무슨 여행이든 간에 빵집 방문은 넣어 놓는거 같아요너무나 유명한 대전의 성심당에 대한 포스팅이랍니다성심당 하면 아직도 부추빵. 튀김소보로만 생각 하시나요!? 하지만 대전 성심당에는 너무나 맛난 빵들이 많아서 이것들만 먹는다면 후회하실거에요!!그중 하나는 카카오순정요새유행하죠!성심당의 찐한 초코 순애보!! 카카오 순정 덩말 맛나요!! 차게 먹으면 더 맛있고요 



어멋 카카오순정도 박스포장이 가능하네요!!





그다음에 포장지가 예뻐서 찍어봤어요성심당에 와서 식빵을 일상처럼 사먹었으몀 좋겠네용!!



이외에도 다양한 성심당 빵한번 구경해보시겠어요!?성심당은 평일에가도 주말에 가도 항상 사람이 북적북적 이겠죠!?



피자빵도 넘나 맛있어보이는넘나 맛난빵이 가득가득



왜 항상 맛집가면 다른 케이블 보면서 뭉ㅇ 드시나 구경하지 않으시나요!?전..빵접시를ㅋㅋㅋ구경했어요생각보다 많이들 담았던 시오팡종류도 많죠!?



먹물방망이!!가격도 그렇게 비싸지않고 일반 제과점 가격인데다먹기엔 저에게 주어진 시간이 너무 적겠죠ㅠㅠ





이건 나중에 꼭먹어볼꺼에요!!플레인크리와상!? 크로와상에 초코입힌건 초코 크라와상인건가!?!?



이건 너무나 귀여워서 찍어봤어요정말 성심당 빵종류 많죠!?!?



근데 조금은 신기했던건전주에서 비빔밥고로케와같은 느낌의밥이..ㅋㅋㅋ있더라도요 맛있나요!?!?



딸기딹한 성심당 빵들도 가득가득





하지만 역시 성심당=튀소 부추빵이겠죠!?!?종류도 정말 다양해요!!!언젠가 부터 튀김 고두마도있더라고요모든 맛난 성심당 빵



주차를 고민한다면! 참고해주세요성심당 가족 브랜드 2곡 이상 이용하시면 통합무료주차권!!기본적으로 1시간 제공됩니다



성심당 빵 못찍은게 반인더 같아여이렇게 샐러드 빵도 있고 정말 다양하거든요!!





결정장애 빵사랑들을 위해서성심당 탑12보문산메아리미스터 홍먹물방망이야채고러케카카



늘 그렇듯 한가한 토요일..집에 우두커니 있다가 갑자기 먹고픈 음식이 띠용 떠올랐다. 그것은 바로 대전의 명물 "성심당"의 튀김소보루!ㅋㅋ 요기조기 다니며 주변분들께서 나눠준 것들 몇번 먹고, 대전역에 있는 성심당 분점에서 몇 번 먹어본게 전부인데...왜 문득 튀김소보루가 떠올랐는지는....세계 9대 불가사의급 미스테리...^^;그냥 먹고팠나보다... 무튼 즉흥적으로 성심당으로 출발~!!날씨가 정말 좋았던 하루!대전토박이이지만...그토록 많은 이들의 입에 오르내리던 성심당에 방문해보는 것은 이번이 처음....ㅋㅋㅋ"부산에사는 사람이 해운대에 잘 가지 않는다"와 같은 이치가 아닐까 합니다(어설픈 합리화..!?) 햇살이 너무나 좋았던 날이라서..막 찍어도 그림 같은 사진이 나오는 듯 해요!ㅋㅋ허세 컷 한장..+ 동시에 광각렌즈 영입하길 잘했다는 뿌듯함이 듭니다..!ㅋㅋ사진으로만 봐도 느껴지는 따스한 햇살! 시간은 흐르고 흘러서 어느덧 긴 팔을 입어야하는 때가 왔네요..ㅠㅠ2015년이 되어...한 해도 열심히 살자는 다짐을 했던 것이 어제같은데 10월 중순이라니 ㅠㅠ약간의 보정을 통해서 더욱 푸르게 보이게끔 만들어 본 사진...보기만해도 기분이 좋아집니다..성심당에 제대로 가본적은 없을지언정, 성심당 앞 거리는 늘 막힌다는 것을 알고 있는 저는성심당 부근에 있는 주차장을 네비게이션으로 찍고 갑니다!성심당 바로 건너편에 위치한 <우리들공원 주차장>요금은 1시간에 1300원....!!

우리들공원 주차장의 위치(주소) 대전광역시 중구 대흥동 215번지(도로명주소 :  대전광역시 중구 중앙로 138번길 30번지)연락처 : (042) - 253 - 4582but..우리들공원 주차장은 성심당 고객을 배려하는 주차장이므로성심당에서 1만원 이상 결제 시 "무려" 1시간 주차 무료!ㅋㅋ소중한 차를 안전히 주차할 수 있다는 점을 감안하면, 1시간에 1300원도 그리 비싼편은 아니지만....무튼 무료라고 하니까 좋네요! 바로 앞에 보이는 골목으로 들어가서 차단기 앞에 잠시 차를 



 
 
대전 성심당 튀김소보로, 대전 성심당 본점에서 맛보다 - 전국 3대 빵집
 
 

 
 
 
안녕하세요. 요리하는남자 홍쓰입니다:)
 
오늘은 지난주말에 다녀온 대전 성심당 튀김소보로를 올립니다~^^
 
 
친구 결혼식으로 대전에 간김에
 
전국 3대 빵집으로 유명한 대전 성심당으로 향했습니다 ㅎㅎ
 
 
너무나도 유명한 성심당은
 
처음 만들어졌을때부터 지금까지 하루에 팔다가 남은빵들을 남기지 않고 불우이웃에게 나누어 주고있답니다
 
하루도 빠짐없이 매일매일 이렇게 하기도 쉽지 않쵸
 
가격도 엄청 클텐데 말이죠~ 그래도 오랜기간 동안 나눔을 실천한 성심당~!!
 
남는 빵이 없기때문에
 
바로만든 신선한 빵을 제공하는 가게라는 믿음이 더욱갑니다~!!!! 
 
 

 

 
 
대전성심당까지 어떻게 가나요? - 주소와 지도 참고하세요



성심당 주소 - 대전 중구 은행동 145
 

 
 
 
성심당 본점 - 3층 규모로 건물이 큽니다~!!
 
 

 
 
 
1956년부터 대전의 그 자리에서 명물로 지키고 있네요~!!
 
들어서자마자 긴줄~~
 
그리고 가득차있는 손님들과 빵들~~!!
 
그냥 보기에도 손님반 빵반입니다~ㅎㅎㅎ
 
 

 
 
 
 그날그날 만든 신선한 다양한 빵들~!!
 
 

 
 
 
시식도 많구요~ㅎㅎ
 
직원분들도 많아서 친절하게 빵을 구입할수가 있습니다
 
성심당빵은
 
한국 빵집 최초로 미슐랭가이드에 선정된 빵입니다
 
 
* 미슐랭가이드 - 일반적으로 알려져있는 레스토랑 정보를 전문적으로 소개하며 레스토랑 등급에 따라 별점을 부여하는
 
여행정보를 소개하는 세계 최고 권위의 여행정보 안내서입니다
 
 

 
 
 
다른 빵도 맛있어 보였지만
 
대전 성심당하면 가장 유명한 튀김소보로 : 튀.소 를 먹어봐야죠~^^
 
바로 나온 튀김소보로를 빠르게 포장하고 계시네요~
 

 
 
 
이 안쪽에서는 
 
튀김소보로와 부추빵을 비롯한 성심당의 모든빵을 만들고 계십니다~~ 위생 철저~!!
 

 
 
 
튀김소보로와 부추



 LG트윈스/대전원정-원정경기를 가장한 대전나들이 ♪ 성심당 튀김소보루,한밭야구장,서대전역 <문선재포수>  사실은 다녀왔던 대전원정경기 VS 한화이글스 다녀왔습니다 ! 원래는 태균오빠 커플까지 해서 4명이서 차로 가려고 했던 원정길이였는데 어찌하다 보니 회사들 때문에 다들 바빠서 파토가 날뻔 하다가 큰온니와 저 둘이 함께 가기로 했어요 ㅎ 우리 둘다 면허도 없고 차도 없는 뚜벅이라 기차를 이용해 다녀오기로 했어요 , KTX 타면 빠르고 좋지만 간만에 여행 느낌내보자며 기차 들 중에서는 가장 칙칙폭폭하다는 무궁화호로 티켓을 구입해서 다녀왔어요 . 야구 이야기로는 진짜 할말없게 만든 경기였지만 그래도 대전나들이가 즐거워 남기는 포스팅 입니다아 , 사진 많고 스압이예요     원래는 차로 가는 대전 원정길이 계획되어 있었지만 급작스럽게 파토가 나는 바람에 선택한 기차로 대전가기 ! 다들 버스를 타고 가라고 했는데 , 집이영등포 이다 보니 오히려 고속터미널 등까지 이동하는 것 보다 훨씬 편해요 늦게 집에 도착해서 집까지 걸어 들어 올 수 있다는 점 때문에 기차로 이동하기로 합니다 .  평소에는 버스로 이동하는 일이 많아서 오랜만에 영등포역 안으로 들어와 본 것 같아요- 이대로 부산까지 가고싶다 ㅠ   큰온니가 생일선물로 준 하와이가방 ! 드디어 나들이용으로 매보게 되었어요 . 그동안은 그냥 출퇴근길에만 맸는데 이번에야 말로 진짜 나들이에 이용하기 - 조금 큼지막한 사이즈 이긴 하지만 여기에 훌라춤 출때 입는 파에로 유니폼 2개 , 응원손가락, 응원 머리띠, 스냅백모자 , 핸드폰 충전기 그외 다양한 물건 들이 다 들어 있습니다.  가끔 매면 너무 좋은 백팩이예요 ♥    오늘의 기차여행 동반자 ! 파토난 대전원정길에도 흔쾌히 기차로 가자! 라고 해주신 LG트윈스 열혈팬 큰온니 입니다. 우리 언니가 어쩌다 이렇게 LG트윈스의 팬이 되었는지 알 수 없지만, 지금은 진짜 우리 중에서 제일로 엄지 촥 !  잘 다녀와 봅시다    대학교때는 정말 자주 종종 기차를 이용했어요



이 큰 상자에 선물받은 느낌♡주말에 애들이랑 성심당 치즈 스콘 키트에 밤잼으로 밤라떼 하려고 어제 주문했는데 예상보다 너무 실한 세뚜세뚜!유남매, 야경 스크래치북은 내일 하자규. 크으 👍큐알코드, 친절해♡연잎차 향긋해 :)향도 맛도 굿굿틴케이스도 실해서 바로 애들 색연필 모아 책상 앞 연필꽂이로 정리했당 ♡백제야경 무드등 대박. 노래도 좋구먼 🙃 불투명 둥근 케이스를 벗기면백제 문양이 빛과 함께 쏟아진다. 대박. 집을 좀 치우고 찍을걸...ㅋ애들이 한참을 가지고 놀았다. 완충하면 2시간 이용 가능하다고. 중간 버튼 1번 누르면 음악 플레이또 한번 누르면 음악 중지길게 누르면 led 조명 플레이 두번 클릭하면 회전 기능까지 ㅎ #대한민국테마여행#여행을배달해드립니다#집콕여행꾸러미#빵삼킨밤#성심당치즈스콘키트https://m.smartstore.naver.com/ofhandsome/products/5390429618?NaPm=ct%3Dkm69lw6j%7Cci%3Dcheckout%7Ctr%3Dppc%7Ctrx%3D%7Chk%3D245566b7258a70b46ea4c40b6a0403ba9a5f5e50


here
포스팅 URL : https://blog.naver.com/0olina0?Redirect=Log&logNo=222273759949
포스팅 제목 : 집콕놀이 키트,  집콕여행꾸러미 '빵 삼킨 밤'
포스팅 설명 : 이 큰 상자에 선물받은 느낌♡ 주말에 애들이랑 성심당 치즈 스콘 키트에 밤잼으로 밤라떼... ㅎ #대한민국테마여행 #여행을배달해드립니다 #집콕여행꾸러미 #빵삼킨밤... 
포스팅 날짜 : 21.03.13
블로거 이름 : 지속적인 관심
포스팅 내용 : 

이 큰 상자에 선물받은 느낌♡주말에 애들이랑 성심당 치즈 스콘 키트에 밤잼으로 밤라떼 하려고 어제 주문했는데 예상보다 너무 실한 세뚜세뚜!유남매, 야경 스크래치북은 내일 하자규. 크으 👍큐알코드, 친절해♡연잎차 향긋해 :)향도 맛도 굿굿틴케이스도 실해서 바로 애들 색연필 모아 책상 앞 연필꽂이로 정리했당

In [5]:
# 네이버 검색 API예제는 블로그를 비롯 전문자료까지 호출방법이 동일하므로 blog검색만 대표로 예제를 올렸습니다.
# 네이버 검색 Open API 예제 - 블로그 검색
import os
import sys
import urllib.request
client_id = naver_client_id
client_secret = naver_client_secret

encText = urllib.parse.quote("오월드 후기")
url = f"https://openapi.naver.com/v1/search/blog?query={encText}&display=100"   # json 결과
# url = "https://openapi.naver.com/v1/search/blog.xml?query=" + encText # xml 결과
request = urllib.request.Request(url)
request.add_header("X-Naver-Client-Id",client_id)
request.add_header("X-Naver-Client-Secret",client_secret)
response = urllib.request.urlopen(request)
rescode = response.getcode()
if(rescode==200):
    response_body = response.read()
    print(response_body.decode('utf-8'))
else:
    print("Error Code:" + rescode)

{
"lastBuildDate": "Tue, 18 May 2021 14:54:11 +0900",
"total": 1499,
"start": 1,
"display": 100,
"items": [
{
"title": "대전 <b>오월드</b> :: 사파리, 조이랜드(놀이기구) 위주 <b>후기</b>",
"link": "https:\/\/blog.naver.com\/mayisle?Redirect=Log&logNo=221643443254",
"description": "저희가 이용했던 사파리, 놀이기구 위주 <b>후기</b> 남겨볼게요. 먼저, 대전 <b>오월드</b> 자유이용권은 가는 길에... 사파리를 나와 계단을 올라가면 주<b>월드</b>와 버드랜드, 플라워랜드가 있는 것 같았어요. 흐린 날이긴... ",
"bloggername": "남쪽 바닷가 이야기",
"bloggerlink": "https://blog.naver.com/mayisle",
"postdate": "20190909"

},
{
"title": "대전 <b>오월드</b> 즐기는 꿀팁 및 <b>후기</b>",
"link": "https:\/\/blog.naver.com\/hwang_geum02?Redirect=Log&logNo=222317079041",
"description": "시간이 없기도 하고 암튼 오늘은 대전의 명소 <b>오월드</b>에 다녀온 <b>후기</b>를 올려보려고 해요~ 대전에서 태어나 자라면서 <b>오월드</b>를 여러번 간적이 있었는데 사파리 투어는 안해봤고 남친이 동물을 또 엄청 조아라 해서... ",
"bloggername": "골든라이프",
"bloggerlink": "https://blog.naver.com/hwang_geum02",
"postdate": "20210420"

},
{
"title": "대전 <b>오월드</b> 플라워랜드&amp;버드랜드 야간개장 <b>후기</b>",
"link": "https:\/\/blog.naver.com\/poll368?Redi